# Use RASA DSL to Configure DeepPavlov's GO-Bot

At DeepPavlov, we support a variety of industry-wide and popular standards to support developing Conversational AI solutions.
DSLs, known as Domain-Specific Languages, provide a rich mechanism to define the behavior, or "the what", while
the underlying system uses the parser to transform these definitions into commands that implement this behavior, or "the how"
using the system's components.
Until very recently we supported two such DSLs, including industry-standard [AIML](http://docs.deeppavlov.ai/en/master/features/skills/aiml_skill.html), as well as [DSL](http://docs.deeppavlov.ai/en/master/features/skills/dsl_skill.html) designed by one our partners, EORA.

In this tutorial, you will learn how to use another industrial DSL, or, better said, set of DSLs, introduced by RASA.ai,
to build simple goal-oriented chatbots using DeepPavlov's GO-bot.

As discussed in our [blog post](todo/link), this is the very beginning of our work focused on supporting RASA DSLs as a way to configure DeepPavlov-based
goal-oriented chatbots, and therefore not all elements of the RASA DSLs are supported. It is also worth mentioning that in this release we want to focus on supporting tools 
to define the domain logic behind the goal-oriented assistant, and files like `config.yml` and others are out of scope for this release.

To configure a DeepPavlov-based goal-oriented chatbot using these DSLs, you need to have at least three basic config files:
* `stories.md` (or `stories-{trn, tst, val}.md` but these are just subsamples)
* `nlu.md`
* `domain.yml`

These files allow you to define 3 key elements of the chatbot, including product-level stories, NLU training data, and your chatbot's domain.

## Concepts Behind Stories.md, NLU.md, and Domain.yml

### `stories.md`



`stories.md` is a mechanism used to teach your chatbot how to respond to user messages. It allows you to control your chatbot's dialog management.

These "stories" model real conversations between a user and a chatbot. This Markdown-based file is used to define a list of
*stories*, and each *story* can have a list of one or more *intents* with (optional) corresponding *slots*, where each *intent*
has one or more corresponding actions taken by the chatbot.

These actions, in general, can be anything, from simple message replies, to programmable actions that call APIs of other services.
*Note:* In this version, supported actions are limited to simple message replies.

In a way, it can be seen as a *dialogues dataset*.

*Note: Stories do not provide an ultimative instruction of how the bot should behave: it is up to the training process to infer the implicit underlying patterns controlling the dialogue.*  
If one looks for the way to make the bot follow the story templates as strict as possible, 
then there is a known hack: 
the more times the model sees the training data, the better the model models the data, 
so the the desired behavior is achieved when the accuracy on the training data is 1.
Such a situation is illustrated in section Basic Chatbot.

#### format

Stories file is a markdown file of the following format:

```markdown
## story_title(not used by algorithm, but useful to work with for humans)
* user_action_label{"1st_slot_present_in_action": "slot1_value", .., "Nth_slot_present_in_action": "slotN_value"}
 - system_respective_utterance
* another_user_action_of_the_same_format
  - another_system_response
...

## another_story_title
...

```

**See examples below in this tutorial**

### `nlu.md`


`nlu.md` represents an NLU model of your chatbot. It allows you to provide training examples that show how your chatbot should
understand user messages, and then train a model through these examples.

While DeepPavlov's GO-bot supports JSON-based DSTC-2 format for training data, this Markdown Format introduced by RASA is the easiest one for humans to read and write.

#### format

NLU file is a markdown file of the following format:

```markdown
## intent:possible_user_action_label_1
- An example of user text that has the possible_user_action_label_1 action label
- Another example of user text that has the possible_user_action_label_1 action label
...

## intent:possible_user_action_label_N
- An example of user text that has the (possible_user_action_label_N)[action_label] action label
<!-- Slotfilling dataset is provided as an inline markup of user texts -->
...

```

**See examples below in this tutorial**

### `domain.yml`

`domain.yml` helps you to define the universe your chatbot lives in: what user inputs it expects to get, what actions it should be able to predict,
how to respond, and what information to store.
This YML format is relatively simple, and it can be seen as a dictionary of all components of your chatbot, including but not limited to intents,
actions, responses, and other things.

#### format

Domain file is a YAML file of the following format:

```yaml
# slots section lists the possible slot names (aka slot types) 
# that are used in the domain (i.e. relevant for bot's tasks)
# currently only type: text is supported
slots:
  slot1_name:
    type: text
  ...
  slotN_name:
    type: text

# entities list now follows the slots list 2nd level keys 
# and is present to support upcoming features. Stay tuned for updates with this!
entities:
- slot1_name
...
- slotN_name

# intents section lists the intents that can appear in the stories
# being kept together they do describe the user-side part of go-bot's experience
intents:
  - user_action_label
  - another_user_action_of_the_same_format
  ...

# responses section lists the system response templates.
# Despite system response' titles being usually informative themselves
#   (one could even find them more appropriate when no actual "Natural Language" is needed 
#    (e.g. for buttons actions in bot apps))
# It is though extremely useful to be able to serialize the response title to text. 
# That's what this section content is needed for.
responses:
  system_utterance_1:
    - text: "The text that system responds with"
  another_system_response:
    - text: "Here some text again"

```

**See examples below in this tutorial**

## Basic Chatbot

Let's build the simplest chatbot possible.
This chatbot will be capable of processing three intents: *greeting*, *goodbye*, and *thanks*.

In [1]:
DP_MIN_DEMO_DIR = "dp_minimal_demo_dir"  # we will work in this folder

In [2]:
import os

%cd /content
os.makedirs(DP_MIN_DEMO_DIR, exist_ok=True)
%cd {DP_MIN_DEMO_DIR}

/content
/content/dp_minimal_demo_dir


### Stories.md: Basic Stories Example

`stories.md` is pretty straightforward in this case. In it you define 3 stories, each having its own intent and response (utterance).
Take into account the fact that you can combine all of these intents under one story, or add two intents to one stories, and third to another one.

In [3]:
%%writefile stories.md

## greet
* greet
  - utter_greet

## thank
* thank
  - utter_noworries

## goodbye
* bye
  - utter_bye

Writing stories.md


### nlu.md: Basic NLU Training Data Example

`nlu.md` has an NLU training data that enables DeepPavlov to recognize user phrases as belonging to one the pre-defined intents.

In [4]:
%%writefile nlu.md

## intent:greet
- Hi
- Hey
- Hi bot
- Hey bot
- Hello
- Good morning
- hi again
- hi folks

## intent:bye
- goodbye
- goodnight
- good bye
- good night
- see ya
- toodle-oo
- bye bye
- gotta go
- farewell

## intent:thank
- Thanks
- Thank you
- Thank you so much
- Thanks bot
- Thanks for that
- cheers


Writing nlu.md


### domain.yml: Basic Domain Example

`domain.yml` lists the list of: 
* possible user action intents 
* possible system response actions

*Note:* Entities and slots are omitted in this example. See the more sophisticated example below to see how they can be defined in the `domain.yml`.

In [5]:
%%writefile domain.yml

intents:
  - greet
  - bye
  - thank

responses:
  utter_noworries:
  - text: No worries!
  utter_greet:
  - text: Hi
  utter_bye:
  - text: Bye!

Writing domain.yml


The next step is to install the `deeppavlov` library.

In [6]:
!pip install git+https://github.com/deepmipt/DeepPavlov.git@feature/gobot-md-yaml-config
!python -m deeppavlov install gobot_simple_dstc2

  Cloning https://github.com/deepmipt/DeepPavlov.git (to revision feature/gobot-md-yaml-config) to /tmp/pip-req-build-cdpoe72e
  Running command git clone -q https://github.com/deepmipt/DeepPavlov.git /tmp/pip-req-build-cdpoe72e
  Running command git checkout -b feature/gobot-md-yaml-config --track origin/feature/gobot-md-yaml-config
  Switched to a new branch 'feature/gobot-md-yaml-config'
  Branch 'feature/gobot-md-yaml-config' set up to track remote branch 'feature/gobot-md-yaml-config' from 'origin'.
     |████████████████████████████████| 51kB 4.4MB/s 
     |████████████████████████████████| 2.1MB 10.5MB/s 
     |████████████████████████████████| 51kB 6.2MB/s 
     |████████████████████████████████| 1.5MB 31.4MB/s 
     |████████████████████████████████| 20.1MB 1.6MB/s 
     |████████████████████████████████| 10.4MB 47.8MB/s 
     |████████████████████████████████| 512kB 49.1MB/s 
     |████████████████████████████████| 7.3MB 46.4MB/s 
     |████████████████████████████████| 51kB 

2020-08-06 11:24:12.217 INFO in 'deeppavlov.core.common.file'['file'] at line 32: Interpreting 'gobot_simple_dstc2' as '/usr/local/lib/python3.6/dist-packages/deeppavlov/configs/go_bot/gobot_simple_dstc2.json'
     |████████████████████████████████| 696kB 7.6MB/s 
     |████████████████████████████████| 10.4MB 7.2MB/s 
     |████████████████████████████████| 2.2MB 42.5MB/s 
  Found existing installation: thinc 7.4.0
    Uninstalling thinc-7.4.0:
      Successfully uninstalled thinc-7.4.0
  Found existing installation: spacy 2.2.4
    Uninstalling spacy-2.2.4:
      Successfully uninstalled spacy-2.2.4
     |████████████████████████████████| 110.5MB 97kB/s 
     |████████████████████████████████| 512kB 6.1MB/s 
     |████████████████████████████████| 3.8MB 17.0MB/s 
     |████████████████████████████████| 51kB 6.6MB/s 
  Created wheel for gast: filename=gast-0.2.2-cp36-none-any.whl size=7540 sha256=8615bab9ac99ec7f6c95ff2c3dbf02497fd2d4a5cb4f60e62797fd34fa65e58a
  Stored in directory: /

Define the path to our DSL-based configuration files above (the folder we are in right now) and the folder used to store the trained bot.

In [7]:

from deeppavlov import configs
from deeppavlov.core.common.file import read_json


gobot_config = read_json(configs.go_bot.gobot_md_yaml_minimal)

gobot_config['metadata']['variables']['DATA_PATH'] = '.'
gobot_config['metadata']['variables']['MODEL_PATH'] = '.'

Since our data is basically the mock tutorial data we will use the same subsamples for all of the train (training set), test (test set) and valid (validation set) subsamples. 

However, for a real system you should use different train, test, and valid sample stories.md files.

In [8]:
!cp stories.md stories-trn.md
!cp stories.md stories-tst.md 
!cp stories.md stories-val.md 

The next step is to train the bot:

In [9]:
from deeppavlov import train_model

train_model(gobot_config, download=True)

2020-08-06 11:25:21.416 INFO in 'deeppavlov.core.data.utils'['utils'] at line 94: Downloading from http://files.deeppavlov.ai/embeddings/glove.6B.100d.txt to /root/.deeppavlov/downloads/embeddings/glove.6B.100d.txt
347MB [00:20, 17.3MB/s]
2020-08-06 11:25:41.791 INFO in 'deeppavlov.core.data.utils'['utils'] at line 94: Downloading from http://files.deeppavlov.ai/datasets/gobot_md_yaml_minimal.tar.gz to /content/gobot_md_yaml_minimal.tar.gz
100%|██████████| 528/528 [00:00<00:00, 1.40MB/s]
2020-08-06 11:25:41.892 INFO in 'deeppavlov.core.data.utils'['utils'] at line 269: Extracting /content/gobot_md_yaml_minimal.tar.gz archive into /content/dp_minimal_demo_dir
2020-08-06 11:25:41.910 DEBUG in 'deeppavlov.dataset_readers.md_yaml_dialogs_reader'['md_yaml_dialogs_reader'] at line 217: BEFORE MLU_MD_DialogsDatasetReader._read_story(): story_fpath=/content/dp_minimal_demo_dir/stories-trn.md, dialogs=False, domain_knowledge=<deeppavlov.dataset_readers.md_yaml_dialogs_reader.DomainKnowledge obj

2020-08-06 11:25:45.539 DEBUG in 'deeppavlov.dataset_readers.md_yaml_dialogs_reader'['md_yaml_dialogs_reader'] at line 217: BEFORE MLU_MD_DialogsDatasetReader._read_story(): story_fpath=/content/dp_minimal_demo_dir/stories-trn.md, dialogs=True, domain_knowledge=<deeppavlov.dataset_readers.md_yaml_dialogs_reader.DomainKnowledge object at 0x7ff1128089e8>, intent2slots2text={'greet': {(): [{'text': 'Hi', 'slots': []}, {'text': 'Hey', 'slots': []}, {'text': 'Hi bot', 'slots': []}, {'text': 'Hey bot', 'slots': []}, {'text': 'Hello', 'slots': []}, {'text': 'Good morning', 'slots': []}, {'text': 'hi again', 'slots': []}, {'text': 'hi folks', 'slots': []}]}, 'bye': {(): [{'text': 'goodbye', 'slots': []}, {'text': 'goodnight', 'slots': []}, {'text': 'good bye', 'slots': []}, {'text': 'good night', 'slots': []}, {'text': 'see ya', 'slots': []}, {'text': 'toodle-oo', 'slots': []}, {'text': 'bye bye', 'slots': []}, {'text': 'gotta go', 'slots': []}, {'text': 'farewell', 'slots': []}]}, 'thank': {(





Instructions for updating:
Use keras.layers.Dense instead.
Instructions for updating:
Please use `layer.__call__` method instead.
Instructions for updating:
This class is equivalent as tf.keras.layers.LSTMCell, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
Please use `keras.layers.RNN(cell)`, which is equivalent to this API
Instructions for updating:
Please use `layer.add_weight` method instead.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where




Instructions for updating:
Use Variable.read_value. Variables in 2.X are initialized automatically both in eager and graph (inside tf.defun) contexts.

Instructions for updating:
Use standard file APIs to check for files with this prefix.


2020-08-06 11:26:26.908 INFO in 'deeppavlov.models.go_bot.policy.policy_network'['policy_network'] at line 89: INSIDE PolicyNetwork init(). Initializing PolicyNetwork from scratch.
2020-08-06 11:26:26.982 INFO in 'deeppavlov.core.trainers.nn_trainer'['nn_trainer'] at line 198: Initial best per_item_action_accuracy of 0.6667


{"valid": {"eval_examples_count": 3, "metrics": {"per_item_action_accuracy": 0.6667}, "time_spent": "0:00:01", "epochs_done": 0, "batches_seen": 0, "train_examples_seen": 0, "impatience": 0, "patience_limit": 10}}


...

2020-08-06 11:27:09.449 INFO in 'deeppavlov.core.data.simple_vocab'['simple_vocab'] at line 115: [loading vocabulary from /content/dp_minimal_demo_dir/word.dict]
2020-08-06 11:27:09.453 DEBUG in 'deeppavlov.dataset_readers.md_yaml_dialogs_reader'['md_yaml_dialogs_reader'] at line 217: BEFORE MLU_MD_DialogsDatasetReader._read_story(): story_fpath=/content/dp_minimal_demo_dir/stories-trn.md, dialogs=True, domain_knowledge=<deeppavlov.dataset_readers.md_yaml_dialogs_reader.DomainKnowledge object at 0x7ff10ac60240>, intent2slots2text={'greet': {(): [{'text': 'Hi', 'slots': []}, {'text': 'Hey', 'slots': []}, {'text': 'Hi bot', 'slots': []}, {'text': 'Hey bot', 'slots': []}, {'text': 'Hello', 'slots': []}, {'text': 'Good morning', 'slots': []}, {'text': 'hi again', 'slots': []}, {'text': 'hi folks', 'slots': []}]}, 'bye': {(): [{'text': 'goodbye', 'slots': []}, {'text': 'goodnight', 'slots': []}, {'text': 'good bye', 'slots': []}, {'text': 'good night', 'slots': []}, {'text': 'see ya', 'slot

{"valid": {"eval_examples_count": 3, "metrics": {"per_item_action_accuracy": 1.0}, "time_spent": "0:00:01"}}
{"test": {"eval_examples_count": 3, "metrics": {"per_item_action_accuracy": 1.0}, "time_spent": "0:00:01"}}


2020-08-06 11:27:09.459 INFO in 'deeppavlov.dataset_readers.dstc2_reader'['dstc2_reader'] at line 112: [loading dialogs from /tmp/tmpu6c3lm5s]
2020-08-06 11:27:09.461 DEBUG in 'deeppavlov.dataset_readers.md_yaml_dialogs_reader'['md_yaml_dialogs_reader'] at line 306: AFTER MLU_MD_DialogsDatasetReader._read_story(): story_fpath=/content/dp_minimal_demo_dir/stories-trn.md, dialogs=True, domain_knowledge=<deeppavlov.dataset_readers.md_yaml_dialogs_reader.DomainKnowledge object at 0x7ff10ac60240>, intent2slots2text={'greet': {(): [{'text': 'Hi', 'slots': []}, {'text': 'Hey', 'slots': []}, {'text': 'Hi bot', 'slots': []}, {'text': 'Hey bot', 'slots': []}, {'text': 'Hello', 'slots': []}, {'text': 'Good morning', 'slots': []}, {'text': 'hi again', 'slots': []}, {'text': 'hi folks', 'slots': []}]}, 'bye': {(): [{'text': 'goodbye', 'slots': []}, {'text': 'goodnight', 'slots': []}, {'text': 'good bye', 'slots': []}, {'text': 'good night', 'slots': []}, {'text': 'see ya', 'slots': []}, {'text': 't

INFO:tensorflow:Restoring parameters from /content/dp_minimal_demo_dir/model/policy


Chainer[<deeppavlov.models.go_bot.wrapper.DialogComponentWrapper at 0x7ff111f24630>,

Finally, it's time to build our bot and experiment with it:

In [10]:
from deeppavlov import build_model
bot = build_model(gobot_config)

2020-08-06 11:27:50.265 INFO in 'deeppavlov.core.data.simple_vocab'['simple_vocab'] at line 115: [loading vocabulary from /content/dp_minimal_demo_dir/word.dict]
2020-08-06 11:27:50.271 DEBUG in 'deeppavlov.dataset_readers.md_yaml_dialogs_reader'['md_yaml_dialogs_reader'] at line 217: BEFORE MLU_MD_DialogsDatasetReader._read_story(): story_fpath=/content/dp_minimal_demo_dir/stories-trn.md, dialogs=True, domain_knowledge=<deeppavlov.dataset_readers.md_yaml_dialogs_reader.DomainKnowledge object at 0x7ff101398f28>, intent2slots2text={'greet': {(): [{'text': 'Hi', 'slots': []}, {'text': 'Hey', 'slots': []}, {'text': 'Hi bot', 'slots': []}, {'text': 'Hey bot', 'slots': []}, {'text': 'Hello', 'slots': []}, {'text': 'Good morning', 'slots': []}, {'text': 'hi again', 'slots': []}, {'text': 'hi folks', 'slots': []}]}, 'bye': {(): [{'text': 'goodbye', 'slots': []}, {'text': 'goodnight', 'slots': []}, {'text': 'good bye', 'slots': []}, {'text': 'good night', 'slots': []}, {'text': 'see ya', 'slot

INFO:tensorflow:Restoring parameters from /content/dp_minimal_demo_dir/model/policy


In [11]:
bot.reset()

bot(["start"])
bot(["Hi"])[0][0].actions_tuple

('utter_greet',)

Our bot answers with "greeting" to our "greeting". How will it respond to some grateful message?

In [12]:
bot.reset()
bot(["start"])

bot(["Thanks!"])[0][0].actions_tuple

('utter_noworries',)

Ok, "no woories" is an expected response. Let's check if the "goodbye" user message is processed with the corresponding reply:

In [13]:
bot.reset()
bot(["start"])

bot_response_actions = bot(["bye"])[0][0].actions_tuple

In [14]:
import yaml

system_utter2text = yaml.load(open("domain.yml"))["responses"]
system_utter2text[bot_response_actions[0]][0]["text"]

'Bye!'

## Advanced Demo: Building a Restaurants Bot inspired by the DSTC Schema-Guided Dialogue Dataset

In [15]:
DP_BIG_DEMO_DIR = "dp_big_demo_dir"  # we'll work in this directory

In [16]:
import os

%cd /content
os.makedirs(DP_BIG_DEMO_DIR, exist_ok=True)
%cd {DP_BIG_DEMO_DIR}

/content
/content/dp_big_demo_dir


While the previous demo was focused on figuring out how to work with the very simple goal-oriented chatbot, the reality of chatbots is rarely that simple. 
Take, for example, the use case for restaurants. People can search for them, ask about the menus, or book tables. These activities require a substancially 
more advanced configuration.

In the purpose of this rather more relastic demo, we decided to go through a rather unusual route. To simplify the process of defining the domain and behavior 
of this chatbot, we took a famous industrial research dataset provided by Google Research known as DSTC, or [Schema Dataset](https://github.com/google-research-datasets/dstc8-schema-guided-dialogue).

This dataset contains a huge number of the annotated human-machine conversations 
crowdsourced in an [M2M manner](https://arxiv.org/pdf/1801.04871.pdf) for various real-life scenarios and domains.

One of these domains is dedicated to *Restaurants*. In it, users are performing a variety of the goal-oriented tasks like searching for restaurants or booking tables via interaction with the bot.

Given the power and elegance of the DSTC format, we took liberty to use our **automatic conversion tool** to directly **transform** its data into the set of _stories.md_, _nlu.md_, _domain.yml_. 

##### Download the data used in this tutorial section

In [17]:
# let's get the mentioned converted Schema-dataset subset
!wget http://files.deeppavlov.ai/datasets/schema_resto_md_yaml_v2.tar.gz
!tar -zxf schema_resto_md_yaml_v2.tar.gz 

--2020-08-06 11:28:31--  http://files.deeppavlov.ai/datasets/schema_resto_md_yaml_v2.tar.gz
Resolving files.deeppavlov.ai (files.deeppavlov.ai)... 93.175.29.74
Connecting to files.deeppavlov.ai (files.deeppavlov.ai)|93.175.29.74|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 100665 (98K) [application/octet-stream]
Saving to: ‘schema_resto_md_yaml_v2.tar.gz’

schema_resto_md_yam 100%[===================>]  98.31K  --.-KB/s    in 0.09s   

2020-08-06 11:28:31 (1.11 MB/s) - ‘schema_resto_md_yaml_v2.tar.gz’ saved [100665/100665]



#### Technical Note: Automatic Conversion from DSTSC Schema Format to RASA DSLs 

Schema dataset is provided in DSTC (dialogue state tracking challenge) challenge [format](https://github.com/google-research-datasets/dstc8-schema-guided-dialogue).
The DSTC format has its own advantages: it is very detailed and allows for various additional info to be incorporated to the dataset itself.

In it, there are two major components - Schema Representation, and Dialog Representation. The first component is dedicated to describing sets of Intents, Slots, and Entities that are used by a given service through an API.
The second component is focused on describing actual dialogs that happen between users and services. It also includes actual labels for the aforementioned Intents, Slots, and Entities defined in the Schema component.

However, while DSTC format is quite rich for building state-of-the-art systems that participate in the annual DSTC competitions, it takes a serious effort for the real-world developers to collect and annotate data in this format.
In contrast, RASA DSLs we're illustrating here are quite different from the DSTC: they are meant to be neat and minimalistic, and to allow developers to define their domains from a rather scarce input information.

As mentioned in the beginning of this part of the tutorial, we've performed an automatical conversion of the Schema Restaurants dataset from the DSTC format to RASA DSL.

#### Slot Filler

Any typical goal-oriented chatbot system uses a standard approach to define the way it works in the form of a pipeline. DeepPavlov's Go-Bot is quite permissive in which components
can be used in it's pipeline; however, Slot Filler is the required one.

Slot Filler, also known as slotfiller, is necessary to recognize and normalize slot-filling information provides in user's utterances.

For example, when user says that she wants to "book a table *in London*", slotfiller's job is to recognize that *London* in this phrase represents the required slot `city`.

For the purposes of this demo, we are providing the pretrained slotfiller for the dataset. See [the small notebook](todo/link) on how the slotfiller was trained.

In [18]:
from deeppavlov import configs, train_model, build_model
from deeppavlov.core.common.file import read_json

!python -m deeppavlov download schema_resto_md_yaml/ner_config.json
!python -m deeppavlov download schema_resto_md_yaml/slotfiller_config.json

slotfill_config = read_json("schema_resto_md_yaml/slotfiller_config.json")
slotfiller = build_model(slotfill_config, download=True)


2020-08-06 11:28:38.134 INFO in 'deeppavlov.core.data.utils'['utils'] at line 94: Downloading from http://files.deeppavlov.ai/deeppavlov_data/schema_ner.tar.gz?config=ner_config to /root/.deeppavlov/schema_ner.tar.gz
100% 1.67M/1.67M [00:00<00:00, 4.42MB/s]
2020-08-06 11:28:38.612 INFO in 'deeppavlov.core.data.utils'['utils'] at line 269: Extracting /root/.deeppavlov/schema_ner.tar.gz archive into /root/.deeppavlov/models
2020-08-06 11:28:39.442 INFO in 'deeppavlov.download'['download'] at line 132: Skipped http://files.deeppavlov.ai/embeddings/glove.6B.100d.txt?config=ner_config download because of matching hashes
2020-08-06 11:28:39.718 INFO in 'deeppavlov.core.data.utils'['utils'] at line 94: Downloading from http://files.deeppavlov.ai/datasets/schema_resto_md_yaml_v2.tar.gz?config=ner_config to /root/.deeppavlov/schema_resto_md_yaml_v2.tar.gz
100% 101k/101k [00:00<00:00, 1.18MB/s]
2020-08-06 11:28:39.894 INFO in 'deeppavlov.core.data.utils'['utils'] at line 269: Extracting /root/.d

2020-08-06 11:28:44.505 INFO in 'deeppavlov.download'['download'] at line 132: Skipped http://files.deeppavlov.ai/deeppavlov_data/schema_ner.tar.gz download because of matching hashes
2020-08-06 11:28:45.304 INFO in 'deeppavlov.download'['download'] at line 132: Skipped http://files.deeppavlov.ai/embeddings/glove.6B.100d.txt download because of matching hashes
2020-08-06 11:28:45.398 INFO in 'deeppavlov.download'['download'] at line 132: Skipped http://files.deeppavlov.ai/datasets/schema_resto_md_yaml_v2.tar.gz download because of matching hashes
2020-08-06 11:28:45.600 INFO in 'deeppavlov.core.data.simple_vocab'['simple_vocab'] at line 115: [loading vocabulary from /root/.deeppavlov/models/schema_ner/word.dict]
2020-08-06 11:28:45.605 INFO in 'deeppavlov.core.data.simple_vocab'['simple_vocab'] at line 115: [loading vocabulary from /root/.deeppavlov/models/schema_ner/tag.dict]
2020-08-06 11:28:45.609 INFO in 'deeppavlov.core.data.simple_vocab'['simple_vocab'] at line 115: [loading voca


Instructions for updating:
Use `tf.keras.layers.Conv2D` instead.
Instructions for updating:
Use `tf.cast` instead.



2020-08-06 11:29:26.671 INFO in 'deeppavlov.core.layers.tf_layers'['tf_layers'] at line 760: 
Warning! tf.contrib.cudnn_rnn.CudnnCompatibleLSTMCell is used. It is okay for inference mode, but if you train your model with this cell it could NOT be used with tf.contrib.cudnn_rnn.CudnnLSTMCell later. 


The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.

Instructions for updating:
This class is equivalent as tf.keras.layers.StackedRNNCells, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
seq_dim is deprecated, use seq_axis instead
Instructions for updating:
batch_dim is deprecated, use batch_axis instead


2020-08-06 11:29:26.772 INFO in 'deeppavlov.core.layers.tf_layers'['tf_layers'] at line 760: 
Warning! tf.contrib.cudnn_rnn.CudnnCompatibleLSTMCell is used. It is okay for inference mode, but if you train your model with this cell it could NOT be used with tf.contrib.cudnn_rnn.CudnnLSTMCell later. 
2020-08-06 11:29:28.839 INFO in 'deeppavlov.core.models.tf_model'['tf_model'] at line 51: [loading model from /root/.deeppavlov/models/schema_ner/model_no_pos]


INFO:tensorflow:Restoring parameters from /root/.deeppavlov/models/schema_ner/model_no_pos


2020-08-06 11:29:28.982 WARNING in 'deeppavlov.core.models.serializable'['serializable'] at line 45: Load path '/root/.deeppavlov/downloads/schema_resto_md_yaml/slotfill.json' differs from save path '/root/.deeppavlov/models/slotfill_dstc2/model' in 'infer' mode for DstcSlotFillingNetwork.


In [19]:
slotfiller(["i'm looking for a thai food somewhere in SFO"])

[{'city': 'SFO', 'cuisine': 'Thai'}]

Seems OK. Let's save our slotfiller config to train and evaluate the restaurants bot, finally.

In [20]:
import json

json.dump(slotfill_config, open('slotfill_config.json', 'wt'))

#### Known Limitations

While slotfilling technology uses the power of the industry-standard Named Entity Recognition (NER) method to recognize key slots in the given phrases, 
the quality of slot recognition could be substantially increased by combining this process with the data already known to you as the developer. 
For example, having a finite list of cities that are supported by a given end-user solution (e.g., several cities in Greater Seattle Area for local restaurant chain) 
aids significantly to the slotfiller. Typically, this information is stored in the database, though it could also be available in loose files like CSV (comma-separated values).

However, in order to focus on the support of the RASA DSLs, we made a decision to omit the support for such data. An additional demo will be provided in consequent releases.

Nevertheless our demo goal-oriented bot should still be able to generalize and use the global patterns in the conversations. 

### Stories.md: Advanced Stories Example

`stories.md`

*Note: As said above, this file has been auto-generated from the DSTC schema.*

*Note: As said above, stories do not provide an ultimative instruction of how the bot should behave: it is up to the training process to infer the implicit underlying patterns controlling the dialogue.*  

Like in the Basic Demo, Stories here define a variety of interactions between user and our bot.

In [21]:
STORIES_FPATH = "schema_resto_md_yaml/stories.md"
!echo "stories file size (lines): $(wc -l {STORIES_FPATH})"

!echo -e '\n\npart of stories file is listed below\n'
!head -500 {STORIES_FPATH} | tail -30

stories file size (lines): 4768 schema_resto_md_yaml/stories.md


part of stories file is listed below

  - utter_INFORM_Cuisine+INFORM_StreetAddress+NOTIFY_SUCCESS
* THANK_YOU+GOODBYE{}
  - utter_GOODBYE

## 25
* hi{}
  - utter_hi
* INFORM_INTENT_Intent{"intent": "FindRestaurants"}
  - utter_REQUEST_City
* INFORM_City{"city": "Oakland"}
  - utter_REQUEST_Cuisine
* INFORM_Cuisine{"cuisine": "Fish"}
  - utter_OFFER_RestaurantName+OFFER_City+INFORM_COUNT_Count
* REQUEST_ALTS{}
  - utter_OFFER_RestaurantName+OFFER_City
* INFORM_PriceRange+REQUEST_ALTS{"price_range": "moderate"}
  - utter_OFFER_RestaurantName+OFFER_City+INFORM_COUNT_Count
* REQUEST_ServesAlcohol+REQUEST_HasLiveMusic{}
  - utter_INFORM_HasLiveMusic+INFORM_ServesAlcohol
* INFORM_INTENT_Intent+SELECT{"intent": "ReserveRestaurant"}
  - utter_REQUEST_Time
* INFORM_PartySize+INFORM_Time{"party_size": "2", "time": "10:30 in the morning"}
  - utter_CONFIRM_RestaurantName+CONFIRM_City+CONFIRM_Time+CONFIRM_PartySize+CONFIRM_Date
* R

### nlu.md: Advanced NLU Training Data Example

`nlu.md`

*Note: As said above, this file has been auto-generated from the DSTC schema.*

Like in the Basic Demo, `nlu.md` shows the examples of user utterances for the supported intent classes.
The slotfilling and NER information is provided in the form of the inline mark-up.

In [22]:
NLU_FPATH = "schema_resto_md_yaml/nlu.md"
!echo "nlu file size (lines): $(wc -l {NLU_FPATH})"

!echo -e '\n\npart of nlu file is listed below\n'
!head -50 {NLU_FPATH} | tail -20

nlu file size (lines): 2147 schema_resto_md_yaml/nlu.md


part of nlu file is listed below

- [Evening 7:15](time) at Mcdonald's.
- [6:15 in the evening](time) at Bistro liaison.
- Let's set it up for [6:30 pm](time) at Sakoon.
- I would like a reservation in [Flames Eatery](restaurant_name) at [19:00](time)
- I'm thinking about Rice Bowl, at [morning 11:30](time)

## intent:REQUEST_Cuisine+AFFIRM
- Sounds great. Do you know if they cook [Taiwanese](cuisine) food?
- yeah. what do they serve?

## intent:AFFIRM
- Yes
- That's great.
- Sure that sounds good.
- That works!
- that would be great.
- That sounds good.
- Yes that works for me
- Sure, that sounds great!
- This is good for me


Let's take a closer look to some specific intent examples.

In [23]:
!grep --no-group-separator -m 10 -A 1 -P "(INFORM_Cuisine|INFORM_City)" {NLU_FPATH}

## intent:INFORM_City+INFORM_INTENT_Intent
- Can you find me somewhere to eat in Dublin?
## intent:INFORM_Cuisine
- Anyone that is [burger](cuisine) like in nature
## intent:INFORM_City+INFORM_Cuisine
- I'm looking for [European](cuisine) food in San Francisco.
## intent:INFORM_Cuisine+INFORM_INTENT_Intent
- I am looking for a [Greek](cuisine) place to eat please.
## intent:INFORM_City
- It's in San Francisco.
## intent:INFORM_Cuisine+REQUEST_ALTS
- I'd like another kind of restaurant. I'd like Sushi.
## intent:INFORM_City+INFORM_Time
- I want a restaurant in Mountain View, and a reservation at 1 o"clock in the afternoon.
## intent:INFORM_PriceRange+INFORM_Cuisine
- I would prefer some [Filipino](cuisine) food which is affordable and not too expensive.
## intent:INFORM_City+INFORM_Time+NEGATE
- No. Please make it for [7:30 pm](time) at Santa Clara.
## intent:INFORM_RestaurantName+INFORM_City+INFORM_Time
- the restaurant is la traviata.i want it in san fran.make it at [6:30 pm](time)


### domain.yml: Advanced Domain Example

`domain.yml`

*Note: As said above, this file has been auto-generated from the DSTC schema.*

The domain file now provides the list of slots and entities relevant for the bot as well as the supported intent classes and system response text templates.

In [24]:
DOMAIN_FPATH = "schema_resto_md_yaml/domain.yml"
!echo "domain file size (lines): $(wc -l {DOMAIN_FPATH})"

!echo -e '\n\nmost of domain file is listed below, just some portion of intents and response templates is skipped \n'
!head -40 {DOMAIN_FPATH} && echo "..."
!grep -B 1 -A 10 responses {DOMAIN_FPATH} && echo "..."
!grep --no-group-separator -A 1 OFFER_City: {DOMAIN_FPATH} && echo "..."
!grep --no-group-separator -A 1 CONFIRM_Time: {DOMAIN_FPATH} && echo "..."

domain file size (lines): 478 schema_resto_md_yaml/domain.yml


most of domain file is listed below, just some portion of intents and response templates is skipped 

slots:
  price_range:
    type: text
  cuisine:
    type: text
  date:
    type: text
  restaurant_name:
    type: text
  intent:
    type: text
  party_size:
    type: text
  time:
    type: text
  has_live_music:
    type: text
  city:
    type: text
  serves_alcohol:
    type: text

entities:
- price_range
- cuisine
- date
- restaurant_name
- intent
- party_size
- time
- has_live_music
- city
- serves_alcohol

intents:
  - INFORM_RestaurantName+INFORM_Time
  - THANK_YOU+GOODBYE
  - INFORM_Time+INFORM_RestaurantName
  - INFORM_PriceRange+REQUEST_ALTS
  - REQUEST_PhoneNumber+REQUEST_StreetAddress+AFFIRM
...

responses:
  utter_REQUEST_Cuisine:
    - text: "What are you in the mood for? {cuisine}? {cuisine}"
  utter_REQUEST_City:
    - text: "What city are you interested in?"
  utter_OFFER_RestaurantName+OFFER_City:
    - 

Now that we have all three key files we can now proceed with training the Go-Bot so let's do it.

In [25]:
from deeppavlov import configs
from deeppavlov.core.common.file import read_json


gobot_config = read_json(configs.go_bot.gobot_md_yaml_minimal)
gobot_config['chainer']['pipe'][-1]['slot_filler'] = {"config_path": "slotfill_config.json"}

gobot_config['metadata']['variables']['DATA_PATH'] = 'schema_resto_md_yaml'
gobot_config['metadata']['variables']['MODEL_PATH'] = '.'

Since our data is the tutorial data we will use the same subsamples for all of train (training set), test (test set), and valid (validation set) subsamples.

However, for a real system you should use different train, test, and valid sample stories.md files.

In [26]:
!cp schema_resto_md_yaml/stories.md schema_resto_md_yaml/stories-trn.md
!cp schema_resto_md_yaml/stories.md schema_resto_md_yaml/stories-tst.md
!cp schema_resto_md_yaml/stories.md schema_resto_md_yaml/stories-val.md

In [27]:
from deeppavlov import train_model

train_model(gobot_config, download=False);

{"train": {"eval_examples_count": 85, "metrics": {"per_item_action_accuracy": 0.6854}, "time_spent": "0:02:56", "epochs_done": 10, "batches_seen": 240, "train_examples_seen": 930, "learning_rate": 0.003, "momentum": 0.95, "loss": 0.6648289680480957}}


2020-08-06 11:34:28.829 INFO in 'deeppavlov.core.trainers.nn_trainer'['nn_trainer'] at line 211: Did not improve on the per_item_action_accuracy of 0.695


{"valid": {"eval_examples_count": 85, "metrics": {"per_item_action_accuracy": 0.6854}, "time_spent": "0:03:00", "epochs_done": 10, "batches_seen": 240, "train_examples_seen": 930, "impatience": 1, "patience_limit": 10}}
{"train": {"eval_examples_count": 85, "metrics": {"per_item_action_accuracy": 0.6711}, "time_spent": "0:03:07", "epochs_done": 11, "batches_seen": 255, "train_examples_seen": 987, "learning_rate": 0.003, "momentum": 0.95, "loss": 0.6231737057367961}}


2020-08-06 11:34:39.897 INFO in 'deeppavlov.core.trainers.nn_trainer'['nn_trainer'] at line 211: Did not improve on the per_item_action_accuracy of 0.695


{"valid": {"eval_examples_count": 85, "metrics": {"per_item_action_accuracy": 0.6711}, "time_spent": "0:03:12", "epochs_done": 11, "batches_seen": 255, "train_examples_seen": 987, "impatience": 2, "patience_limit": 10}}
{"train": {"eval_examples_count": 85, "metrics": {"per_item_action_accuracy": 0.7093}, "time_spent": "0:03:18", "epochs_done": 12, "batches_seen": 270, "train_examples_seen": 1044, "learning_rate": 0.003, "momentum": 0.95, "loss": 0.5779090285301208}}


...

{"test": {"eval_examples_count": 85, "metrics": {"per_item_action_accuracy": 0.7344}, "time_spent": "0:00:05"}}


2020-08-06 11:39:25.741 DEBUG in 'deeppavlov.dataset_readers.md_yaml_dialogs_reader'['md_yaml_dialogs_reader'] at line 260: INSIDE MLU_MD_DialogsDatasetReader._read_story(): Skipping story w. line * INFORM_RestaurantName+INFORM_City+INFORM_PartySize{"restaurant_name": "Pearl River", "city": "San Jose", "party_size": "1"} because of no NLU candidates found
2020-08-06 11:39:25.742 DEBUG in 'deeppavlov.dataset_readers.md_yaml_dialogs_reader'['md_yaml_dialogs_reader'] at line 260: INSIDE MLU_MD_DialogsDatasetReader._read_story(): Skipping story w. line * INFORM_PartySize+NEGATE{"party_size": "2"} because of no NLU candidates found
2020-08-06 11:39:25.744 DEBUG in 'deeppavlov.dataset_readers.md_yaml_dialogs_reader'['md_yaml_dialogs_reader'] at line 260: INSIDE MLU_MD_DialogsDatasetReader._read_story(): Skipping story w. line * INFORM_Time+INFORM_Date+INFORM_INTENT_Intent{"time": "seven pm", "date": "9th of this month", "intent": "ReserveRestaurant"} because of no NLU candidates found
2020-0

INFO:tensorflow:Restoring parameters from /root/.deeppavlov/models/schema_ner/model_no_pos


2020-08-06 11:40:10.607 WARNING in 'deeppavlov.core.models.serializable'['serializable'] at line 45: Load path '/root/.deeppavlov/downloads/schema_resto_md_yaml/slotfill.json' differs from save path '/root/.deeppavlov/models/slotfill_dstc2/model' in 'infer' mode for DstcSlotFillingNetwork.
2020-08-06 11:40:10.611 INFO in 'deeppavlov.models.embedders.glove_embedder'['glove_embedder'] at line 52: [loading GloVe embeddings from `/root/.deeppavlov/downloads/embeddings/glove.6B.100d.txt`]
2020-08-06 11:40:51.716 INFO in 'deeppavlov.models.go_bot.policy.policy_network'['policy_network'] at line 86: INSIDE PolicyNetwork init(). Initializing PolicyNetwork from checkpoint.
2020-08-06 11:40:51.724 INFO in 'deeppavlov.core.models.tf_model'['tf_model'] at line 51: [loading model from /content/dp_big_demo_dir/model/policy]


INFO:tensorflow:Restoring parameters from /content/dp_big_demo_dir/model/policy


In [28]:
bot = build_model(gobot_config)

2020-08-06 11:40:51.901 INFO in 'deeppavlov.core.data.simple_vocab'['simple_vocab'] at line 115: [loading vocabulary from /content/dp_big_demo_dir/word.dict]
2020-08-06 11:40:51.936 DEBUG in 'deeppavlov.dataset_readers.md_yaml_dialogs_reader'['md_yaml_dialogs_reader'] at line 217: BEFORE MLU_MD_DialogsDatasetReader._read_story(): story_fpath=/content/dp_big_demo_dir/schema_resto_md_yaml/stories-trn.md, dialogs=True, domain_knowledge=<deeppavlov.dataset_readers.md_yaml_dialogs_reader.DomainKnowledge object at 0x7ff0d0fecf98>, intent2slots2text={'hi': {(): [{'text': 'hi', 'slots': []}, {'text': 'hello', 'slots': []}]}, 'INFORM_City+INFORM_INTENT_Intent': {(): [{'text': 'Can you find me somewhere to eat in Dublin?', 'slots': []}, {'text': 'I want to go out to eat in Milpitas.', 'slots': []}, {'text': 'I would like to make a restaurant reservation in San Jose.', 'slots': []}, {'text': 'I have a friend visiting from out of town and need to find somewhere good for us to eat. Can you look up 

INFO:tensorflow:Restoring parameters from /root/.deeppavlov/models/schema_ner/model_no_pos


2020-08-06 11:41:37.49 WARNING in 'deeppavlov.core.models.serializable'['serializable'] at line 45: Load path '/root/.deeppavlov/downloads/schema_resto_md_yaml/slotfill.json' differs from save path '/root/.deeppavlov/models/slotfill_dstc2/model' in 'infer' mode for DstcSlotFillingNetwork.
2020-08-06 11:41:37.54 INFO in 'deeppavlov.models.embedders.glove_embedder'['glove_embedder'] at line 52: [loading GloVe embeddings from `/root/.deeppavlov/downloads/embeddings/glove.6B.100d.txt`]
2020-08-06 11:42:16.926 INFO in 'deeppavlov.models.go_bot.policy.policy_network'['policy_network'] at line 86: INSIDE PolicyNetwork init(). Initializing PolicyNetwork from checkpoint.
2020-08-06 11:42:16.934 INFO in 'deeppavlov.core.models.tf_model'['tf_model'] at line 51: [loading model from /content/dp_big_demo_dir/model/policy]


INFO:tensorflow:Restoring parameters from /content/dp_big_demo_dir/model/policy


Let's see whether the bot works at all

In [29]:
bot.reset()

bot(["Hey!"])[0][0].actions_tuple

bot.reset()

Ok let's perform a conversation

In [30]:
bot.reset()

bot(["Hey!"])[0][0].actions_tuple

('utter_hi',)

Ok the bot performs OK on greeting

In [31]:
bot(["I'd like to find a restaurant for this evening"])[0][0].actions_tuple

('utter_REQUEST_RestaurantName',)

The bot asks for an inevitably necessary information.

In [32]:
bot(["Somewhere in Oakland, sushi and for two people please"])[0][0].actions_tuple

('utter_CONFIRM_RestaurantName',
 'CONFIRM_City',
 'CONFIRM_Time',
 'CONFIRM_PartySize',
 'CONFIRM_Date')

And so on.

In [33]:
bot(["Cool! That's what I was looking for, thanks!"])[0][0].actions_tuple

('utter_CONFIRM_Time', 'CONFIRM_Date')

Let's say goodbye to our bot

In [34]:
bot(["Bye bot"])[0][0].actions_tuple

('utter_NOTIFY_SUCCESS',)

After the goodbye bot does perform uninterpretable. That's what most of recurrent system do after the end of the sequence cause no one reaches that poing. 

In [35]:
bot(["Bye bot"])[0][0].actions_tuple

('utter_NOTIFY_SUCCESS',)

## Final words

More of in-depth examples of goal-oriented bots and their features are coming with future releases, stay tuned!